In [138]:
import pandas as pd
import glob
import spacy
from spacy.tokens import Span
import os

In [139]:
def join_words(group):
    return ' '.join(group.astype(str))

def create_spacy_training_data(file_path):
    # Load data from the Excel file
    data = pd.read_excel(file_path)
    # if "Line_ID" in data.columns:
    #     group_col = "Line_ID"
    if "ACT" in data.columns:
        group_col = "ACT"
    elif "Original_Act_ID" in data.columns:
        group_col = "Original_Act_ID"
    else:
        "unknown"
    data = data[~data['Word_x'].apply(lambda x: isinstance(x, int))]
    data = data[~data['Word_x'].apply(lambda x: isinstance(x, float))]




    
    # Combine words into sentences, assumed by unique 'Line_ID'
    grouped_data = data.groupby(group_col)['Word_x'].apply(' '.join).reset_index()
    
    # Prepare training data in spaCy format
    training_data = []
    
    for _, row in grouped_data.iterrows():
        text = row['Word_x']
        entities = []
        current_position = 0

        # Iterate over words in the current line to build entities
        for _, word_data in data[data[group_col] == row[group_col]].iterrows():
            start = current_position
            end = start + len(word_data['Word_x'])
            # Check if there's a named entity
            if word_data['LOC_x'] != 'O':
                entities.append((start, end, 'LOC'))
            if word_data['PERS_x'] != 'O':
                entities.append((start, end, 'PER'))
            
            current_position = end + 1  # Update position, accounting for space

        # Append to training data
        training_data.append({"text": text, "entities": entities})
    training_data = convert_to_spacy_docs(training_data)
    return training_data

def convert_to_spacy_docs(training_data):
    # Load spaCy model, you can change it to whatever model you'd like to use or just use a blank one
    nlp = spacy.blank('en')  # Assuming the data is in English; change the language code if needed
    
    # List to hold the spaCy docs
    spacy_docs = []
    
    for record in training_data:
        # Create a doc from the text
        doc = nlp(record['text'])
        
        # Create a list to collect entity spans
        spans = []
        
        for start, end, label in record['entities']:
            span = doc.char_span(start, end, label=label)
            if span is not None:  # Only add the span if it's correctly aligned with token boundaries
                spans.append(span)
        
        # Overwrite the doc's 'ents' with our list of spans
        try:
            doc.spans["sc"] = spans
        except:
            ValueError
            print(spans)
            
        span_ents = []
        for span in doc.spans["sc"]:
            span_ents.append({"text": span.text, "label": span.label_, "start": span.start, "end": span.end})
        # Append the modified doc to the list
        spacy_docs.append({"text": doc.text, 'spans': span_ents})
    
    return spacy_docs

In [140]:
files = glob.glob("Database/*/CONLL/*.xlsx")
print(len(files))

17


In [141]:
training_data = []
for i, filename in enumerate(files):
    manuscript = os.path.basename(filename).split('_final_version_inner')[0]
    print(i, manuscript)
    res = create_spacy_training_data(filename)
    for r in res:
        r["ms"] = manuscript
        training_data.append(r)

0 Notre_Dame_Roche_Paris_BnF_10996
1 Pontoise_Paris_BnF_5657
2 Saint_Denis_Paris_AN_LL_1157
3 Pontigny_Paris_BnF_lat_9887_inner_unmerged.xlsx
4 Navarre_Pau_AD_E513
5 Clairmarais_Troyes_AD_3H3700_inner_unmerged.xlsx
6 Port_Royal_2_Paris_BnF_10998
7 Nesle_Chantilly_GB_Reg12_14F22
8 Fervaques_Paris_BnF_lat_11071
9 Molesme_2_Dijon_ADCO_Cart_143_7H7
10 Saint_Nicaise_Reims_BM_1843_inner_unmerged.xlsx
11 Sommereux_Paris_Bnf_nal_1934
12 Chartres_2_Paris_BnF_lat_10095
13 Chartres_1_Paris_BnF_lat_10094
14 Vauluisant_Paris_BnF_lat_9901
15 Port_Royal_1_Paris_BnF_10997
16 Molesme_1_Dijon_ADCO_Cart_142_7H6


In [142]:
srsly.write_jsonl("home-alcar-ner.jsonl", training_data)